# Zadanie 8 - Alexnet + Dropout & BatchRegularization
### Aleksandra Jonas, Aleksandra Gronowska, Iwona Christop

## Przygotowanie danych

In [1]:
from IPython.display import Image, display

In [2]:
import sys
import subprocess
import pkg_resources
import numpy as np

required = { 'scikit-image'}
installed = {pkg.key for pkg in pkg_resources.working_set}
missing = required - installed
# Alexnet requires images to be of dim = (227, 227, 3)
newSize = (227,227)

if missing: 
    python = sys.executable
    subprocess.check_call([python, '-m', 'pip', 'install', *missing], stdout=subprocess.DEVNULL)

def load_train_data(input_dir):
    import numpy as np
    import pandas as pd
    import os
    from skimage.io import imread
    import cv2 as cv
    from pathlib import Path
    import random
    from shutil import copyfile, rmtree
    import json

    import seaborn as sns
    import matplotlib.pyplot as plt

    import matplotlib
    
    image_dir = Path(input_dir)
    categories_name = []
    for file in os.listdir(image_dir):
        d = os.path.join(image_dir, file)
        if os.path.isdir(d):
            categories_name.append(file)

    folders = [directory for directory in image_dir.iterdir() if directory.is_dir()]

    train_img = []
    categories_count=[]
    labels=[]
    for i, direc in enumerate(folders):
        count = 0
        for obj in direc.iterdir():
            if os.path.isfile(obj) and os.path.basename(os.path.normpath(obj)) != 'desktop.ini':
                labels.append(os.path.basename(os.path.normpath(direc)))
                count += 1
                img = imread(obj)#zwraca ndarry postaci xSize x ySize x colorDepth
                img = img[:, :, :3]
                img = cv.resize(img, newSize, interpolation=cv.INTER_AREA)# zwraca ndarray
                img = img / 255 #normalizacja
                train_img.append(img)
        categories_count.append(count)
    X={}
    X["values"] = np.array(train_img)
    X["categories_name"] = categories_name
    X["categories_count"] = categories_count
    X["labels"]=labels
    return X

def load_test_data(input_dir):
    import numpy as np
    import pandas as pd
    import os
    from skimage.io import imread
    import cv2 as cv
    from pathlib import Path
    import random
    from shutil import copyfile, rmtree
    import json

    import seaborn as sns
    import matplotlib.pyplot as plt

    import matplotlib

    image_path = Path(input_dir)

    labels_path = image_path.parents[0] / 'test_labels.json'

    jsonString = labels_path.read_text()
    objects = json.loads(jsonString)

    categories_name = []
    categories_count=[]
    count = 0
    c = objects[0]['value']
    for e in  objects:
        if e['value'] != c:
            categories_count.append(count)
            c = e['value']
            count = 1
        else:
            count += 1
        if not e['value'] in categories_name:
            categories_name.append(e['value'])

    categories_count.append(count)
    
    test_img = []

    labels=[]
    for e in objects:
        p = image_path / e['filename']
        img = imread(p)#zwraca ndarry postaci xSize x ySize x colorDepth
        img = img[:, :, :3]
        img = cv.resize(img, newSize, interpolation=cv.INTER_AREA)# zwraca ndarray
        img = img / 255#normalizacja
        test_img.append(img)
        labels.append(e['value'])

    X={}
    X["values"] = np.array(test_img)
    X["categories_name"] = categories_name
    X["categories_count"] = categories_count
    X["labels"]=labels
    return X

In [3]:
# Data load
data_train = load_train_data("./train_test_sw/train_sw")
values_train = data_train['values']
labels_train = data_train['labels']

data_test = load_test_data("./train_test_sw/test_sw")
X_test = data_test['values']
y_test = data_test['labels']

In [4]:
from sklearn.model_selection import train_test_split

In [5]:
X_train, X_validate, y_train, y_validate = train_test_split(values_train, labels_train, test_size=0.2, random_state=42)

In [6]:
from sklearn.preprocessing import LabelEncoder

In [7]:
class_le = LabelEncoder()
y_train_enc = class_le.fit_transform(y_train)
y_validate_enc = class_le.fit_transform(y_validate)
y_test_enc = class_le.fit_transform(y_test)

In [8]:
import tensorflow as tf

In [9]:
train_ds = tf.data.Dataset.from_tensor_slices((X_train, y_train_enc))
validation_ds = tf.data.Dataset.from_tensor_slices((X_validate, y_validate_enc))
test_ds = tf.data.Dataset.from_tensor_slices((X_test, y_test_enc))

In [10]:
train_ds_size = tf.data.experimental.cardinality(train_ds).numpy()
test_ds_size = tf.data.experimental.cardinality(test_ds).numpy()
validation_ds_size = tf.data.experimental.cardinality(validation_ds).numpy()
print("Training data size:", train_ds_size)
print("Test data size:", test_ds_size)
print("Validation data size:", validation_ds_size)

Training data size: 820
Test data size: 259
Validation data size: 206


In [11]:
train_ds = (train_ds
                  .shuffle(buffer_size=train_ds_size)
                  .batch(batch_size=32, drop_remainder=True))
test_ds = (test_ds
                  .shuffle(buffer_size=train_ds_size)
                  .batch(batch_size=32, drop_remainder=True))
validation_ds = (validation_ds
                  .shuffle(buffer_size=train_ds_size)
                  .batch(batch_size=32, drop_remainder=True))

In [12]:
from tensorflow import keras
import os
import time

In [13]:
root_logdir = os.path.join(os.curdir, "logs\\fit\\")
def get_run_logdir():
    run_id = time.strftime("run_%Y_%m_%d-%H_%M_%S")
    return os.path.join(root_logdir, run_id)
run_logdir = get_run_logdir()
tensorboard_cb = keras.callbacks.TensorBoard(run_logdir)

## Dropout

### Do warstw spłaszczonych

In [14]:
model_flat_drop = keras.models.Sequential([
    keras.layers.Conv2D(filters=96, kernel_size=(11,11), strides=(4,4), activation='relu', input_shape=(227,227,3)),
    keras.layers.MaxPool2D(pool_size=(3,3), strides=(2,2)),
    keras.layers.Conv2D(filters=256, kernel_size=(5,5), strides=(1,1), activation='relu', padding="same"),
    keras.layers.MaxPool2D(pool_size=(3,3), strides=(2,2)),
    keras.layers.Conv2D(filters=384, kernel_size=(3,3), strides=(1,1), activation='relu', padding="same"),
    keras.layers.Conv2D(filters=384, kernel_size=(3,3), strides=(1,1), activation='relu', padding="same"),
    keras.layers.Conv2D(filters=256, kernel_size=(3,3), strides=(1,1), activation='relu', padding="same"),
    keras.layers.MaxPool2D(pool_size=(3,3), strides=(2,2)),
    keras.layers.Flatten(),
    keras.layers.Dense(4096, activation='relu'),
    keras.layers.Dropout(.5),
    keras.layers.Dense(4096, activation='relu'),
    keras.layers.Dropout(.5),
    keras.layers.Dense(10, activation='softmax')
])

In [15]:
model_flat_drop.compile(loss='sparse_categorical_crossentropy', optimizer=tf.optimizers.SGD(lr=.001), metrics=['accuracy'])
model_flat_drop.summary()

Model: "sequential"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 conv2d (Conv2D)             (None, 55, 55, 96)        34944     
                                                                 
 max_pooling2d (MaxPooling2D  (None, 27, 27, 96)       0         
 )                                                               
                                                                 
 conv2d_1 (Conv2D)           (None, 27, 27, 256)       614656    
                                                                 
 max_pooling2d_1 (MaxPooling  (None, 13, 13, 256)      0         
 2D)                                                             
                                                                 
 conv2d_2 (Conv2D)           (None, 13, 13, 384)       885120    
                                                                 
 conv2d_3 (Conv2D)           (None, 13, 13, 384)       1

In [16]:
model_flat_drop.fit(train_ds,
          epochs=100,
          validation_data=validation_ds,
          validation_freq=1,
          callbacks=[tensorboard_cb])

Epoch 1/100
25/25 [==============================] - 39s 1s/step - loss: 2.2584 - accuracy: 0.2000 - val_loss: 2.1890 - val_accuracy: 0.3073
Epoch 2/100
25/25 [==============================] - 33s 1s/step - loss: 1.9739 - accuracy: 0.2275 - val_loss: 1.6961 - val_accuracy: 0.1875
Epoch 3/100
25/25 [==============================] - 33s 1s/step - loss: 1.6904 - accuracy: 0.2288 - val_loss: 1.6021 - val_accuracy: 0.2604
Epoch 4/100
25/25 [==============================] - 34s 1s/step - loss: 1.6571 - accuracy: 0.2138 - val_loss: 1.5939 - val_accuracy: 0.3333
Epoch 5/100
25/25 [==============================] - 34s 1s/step - loss: 1.6340 - accuracy: 0.2400 - val_loss: 1.5403 - val_accuracy: 0.3438
Epoch 6/100
25/25 [==============================] - 34s 1s/step - loss: 1.6254 - accuracy: 0.2650 - val_loss: 1.5925 - val_accuracy: 0.2917
Epoch 7/100
25/25 [==============================] - 34s 1s/step - loss: 1.6075 - accuracy: 0.2600 - val_loss: 1.5318 - val_accuracy: 0.3698
Epoch 8/100
2

In [17]:
model_flat_drop.evaluate(test_ds)

8/8 [==============================] - 8s 256ms/step - loss: 0.5354 - accuracy: 0.8008


[0.535420835018158, 0.80078125]

### Do warstw maxpooling

In [18]:
model_pool_drop = keras.models.Sequential([
    keras.layers.Conv2D(filters=96, kernel_size=(11,11), strides=(4,4), activation='relu', input_shape=(227,227,3)),
    keras.layers.MaxPool2D(pool_size=(3,3), strides=(2,2)),
    keras.layers.Dropout(.5),
    keras.layers.Conv2D(filters=256, kernel_size=(5,5), strides=(1,1), activation='relu', padding="same"),
    keras.layers.MaxPool2D(pool_size=(3,3), strides=(2,2)),
    keras.layers.Dropout(.5),
    keras.layers.Conv2D(filters=384, kernel_size=(3,3), strides=(1,1), activation='relu', padding="same"),
    keras.layers.Conv2D(filters=384, kernel_size=(3,3), strides=(1,1), activation='relu', padding="same"),
    keras.layers.Conv2D(filters=256, kernel_size=(3,3), strides=(1,1), activation='relu', padding="same"),
    keras.layers.MaxPool2D(pool_size=(3,3), strides=(2,2)),
    keras.layers.Dropout(.5),
    keras.layers.Flatten(),
    keras.layers.Dense(4096, activation='relu'),
    keras.layers.Dense(4096, activation='relu'),
    keras.layers.Dense(10, activation='softmax')
])

In [19]:
model_pool_drop.compile(loss='sparse_categorical_crossentropy', optimizer=tf.optimizers.SGD(lr=.001), metrics=['accuracy'])
model_pool_drop.summary()

Model: "sequential_1"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 conv2d_5 (Conv2D)           (None, 55, 55, 96)        34944     
                                                                 
 max_pooling2d_3 (MaxPooling  (None, 27, 27, 96)       0         
 2D)                                                             
                                                                 
 dropout_2 (Dropout)         (None, 27, 27, 96)        0         
                                                                 
 conv2d_6 (Conv2D)           (None, 27, 27, 256)       614656    
                                                                 
 max_pooling2d_4 (MaxPooling  (None, 13, 13, 256)      0         
 2D)                                                             
                                                                 
 dropout_3 (Dropout)         (None, 13, 13, 256)      

In [20]:
model_pool_drop.fit(train_ds,
          epochs=100,
          validation_data=validation_ds,
          validation_freq=1,
          callbacks=[tensorboard_cb])

Epoch 1/100
25/25 [==============================] - 38s 1s/step - loss: 2.1540 - accuracy: 0.1675 - val_loss: 2.0134 - val_accuracy: 0.1979
Epoch 2/100
25/25 [==============================] - 37s 1s/step - loss: 1.6939 - accuracy: 0.2037 - val_loss: 1.7293 - val_accuracy: 0.1875
Epoch 3/100
25/25 [==============================] - 35s 1s/step - loss: 1.6265 - accuracy: 0.2512 - val_loss: 1.7483 - val_accuracy: 0.2031
Epoch 4/100
25/25 [==============================] - 34s 1s/step - loss: 1.6241 - accuracy: 0.2463 - val_loss: 1.7277 - val_accuracy: 0.2135
Epoch 5/100
25/25 [==============================] - 34s 1s/step - loss: 1.6075 - accuracy: 0.2675 - val_loss: 1.6551 - val_accuracy: 0.2292
Epoch 6/100
25/25 [==============================] - 34s 1s/step - loss: 1.5647 - accuracy: 0.3025 - val_loss: 1.6350 - val_accuracy: 0.4219
Epoch 7/100
25/25 [==============================] - 36s 1s/step - loss: 1.5461 - accuracy: 0.2937 - val_loss: 1.6199 - val_accuracy: 0.2812
Epoch 8/100
2

In [21]:
model_pool_drop.evaluate(test_ds)

8/8 [==============================] - 3s 278ms/step - loss: 0.6054 - accuracy: 0.7578


[0.6054161787033081, 0.7578125]

### Do warstw splotowych

In [22]:
model_conv_drop = keras.models.Sequential([
    keras.layers.Conv2D(filters=96, kernel_size=(11,11), strides=(4,4), activation='relu', input_shape=(227,227,3)),
    keras.layers.Dropout(.5),
    keras.layers.MaxPool2D(pool_size=(3,3), strides=(2,2)),
    keras.layers.Conv2D(filters=256, kernel_size=(5,5), strides=(1,1), activation='relu', padding="same"),
    keras.layers.Dropout(.5),
    keras.layers.MaxPool2D(pool_size=(3,3), strides=(2,2)),
    keras.layers.Conv2D(filters=384, kernel_size=(3,3), strides=(1,1), activation='relu', padding="same"),
    keras.layers.Dropout(.5),
    keras.layers.Conv2D(filters=384, kernel_size=(3,3), strides=(1,1), activation='relu', padding="same"),
    keras.layers.Dropout(.5),
    keras.layers.Conv2D(filters=256, kernel_size=(3,3), strides=(1,1), activation='relu', padding="same"),
    keras.layers.Dropout(.5),
    keras.layers.MaxPool2D(pool_size=(3,3), strides=(2,2)),
    keras.layers.Flatten(),
    keras.layers.Dense(4096, activation='relu'),
    keras.layers.Dense(4096, activation='relu'),
    keras.layers.Dense(10, activation='softmax')
])

In [23]:
model_conv_drop.compile(loss='sparse_categorical_crossentropy', optimizer=tf.optimizers.SGD(lr=.001), metrics=['accuracy'])
model_conv_drop.summary()

Model: "sequential_2"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 conv2d_10 (Conv2D)          (None, 55, 55, 96)        34944     
                                                                 
 dropout_5 (Dropout)         (None, 55, 55, 96)        0         
                                                                 
 max_pooling2d_6 (MaxPooling  (None, 27, 27, 96)       0         
 2D)                                                             
                                                                 
 conv2d_11 (Conv2D)          (None, 27, 27, 256)       614656    
                                                                 
 dropout_6 (Dropout)         (None, 27, 27, 256)       0         
                                                                 
 max_pooling2d_7 (MaxPooling  (None, 13, 13, 256)      0         
 2D)                                                  

In [24]:
model_conv_drop.fit(train_ds,
          epochs=100,
          validation_data=validation_ds,
          validation_freq=1,
          callbacks=[tensorboard_cb])

Epoch 1/100
25/25 [==============================] - 39s 1s/step - loss: 1.8422 - accuracy: 0.2313 - val_loss: 2.1335 - val_accuracy: 0.2604
Epoch 2/100
25/25 [==============================] - 37s 1s/step - loss: 1.7023 - accuracy: 0.2837 - val_loss: 2.0904 - val_accuracy: 0.2969
Epoch 3/100
25/25 [==============================] - 37s 1s/step - loss: 1.5376 - accuracy: 0.3313 - val_loss: 2.0778 - val_accuracy: 0.2292
Epoch 4/100
25/25 [==============================] - 37s 1s/step - loss: 1.4663 - accuracy: 0.3800 - val_loss: 2.0102 - val_accuracy: 0.3542
Epoch 5/100
25/25 [==============================] - 37s 1s/step - loss: 1.4467 - accuracy: 0.3938 - val_loss: 1.9956 - val_accuracy: 0.3073
Epoch 6/100
25/25 [==============================] - 38s 1s/step - loss: 1.2621 - accuracy: 0.4863 - val_loss: 1.8875 - val_accuracy: 0.3333
Epoch 7/100
25/25 [==============================] - 37s 1s/step - loss: 1.2946 - accuracy: 0.4675 - val_loss: 1.8695 - val_accuracy: 0.3958
Epoch 8/100
2

In [25]:
model_conv_drop.evaluate(test_ds)

8/8 [==============================] - 3s 289ms/step - loss: 0.9870 - accuracy: 0.5664


[0.9869575500488281, 0.56640625]

### Do warstw spłaszczonych i maxpooling

In [26]:
model_flat_pool_drop = keras.models.Sequential([
    keras.layers.Conv2D(filters=96, kernel_size=(11,11), strides=(4,4), activation='relu', input_shape=(227,227,3)),
    keras.layers.MaxPool2D(pool_size=(3,3), strides=(2,2)),
    keras.layers.Dropout(.5),
    keras.layers.Conv2D(filters=256, kernel_size=(5,5), strides=(1,1), activation='relu', padding="same"),
    keras.layers.MaxPool2D(pool_size=(3,3), strides=(2,2)),
    keras.layers.Dropout(.5),
    keras.layers.Conv2D(filters=384, kernel_size=(3,3), strides=(1,1), activation='relu', padding="same"),
    keras.layers.Conv2D(filters=384, kernel_size=(3,3), strides=(1,1), activation='relu', padding="same"),
    keras.layers.Conv2D(filters=256, kernel_size=(3,3), strides=(1,1), activation='relu', padding="same"),
    keras.layers.MaxPool2D(pool_size=(3,3), strides=(2,2)),
    keras.layers.Dropout(.5),
    keras.layers.Flatten(),
    keras.layers.Dense(4096, activation='relu'),
    keras.layers.Dropout(.5),
    keras.layers.Dense(4096, activation='relu'),
    keras.layers.Dropout(.5),
    keras.layers.Dense(10, activation='softmax')
])

In [27]:
model_flat_pool_drop.compile(loss='sparse_categorical_crossentropy', optimizer=tf.optimizers.SGD(lr=.001), metrics=['accuracy'])
model_flat_pool_drop.summary()

Model: "sequential_3"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 conv2d_15 (Conv2D)          (None, 55, 55, 96)        34944     
                                                                 
 max_pooling2d_9 (MaxPooling  (None, 27, 27, 96)       0         
 2D)                                                             
                                                                 
 dropout_10 (Dropout)        (None, 27, 27, 96)        0         
                                                                 
 conv2d_16 (Conv2D)          (None, 27, 27, 256)       614656    
                                                                 
 max_pooling2d_10 (MaxPoolin  (None, 13, 13, 256)      0         
 g2D)                                                            
                                                                 
 dropout_11 (Dropout)        (None, 13, 13, 256)      

In [28]:
model_flat_pool_drop.fit(train_ds,
          epochs=100,
          validation_data=validation_ds,
          validation_freq=1,
          callbacks=[tensorboard_cb])

Epoch 1/100
25/25 [==============================] - 37s 1s/step - loss: 2.0917 - accuracy: 0.1775 - val_loss: 1.9565 - val_accuracy: 0.2708
Epoch 2/100
25/25 [==============================] - 34s 1s/step - loss: 1.7322 - accuracy: 0.2000 - val_loss: 1.8304 - val_accuracy: 0.3177
Epoch 3/100
25/25 [==============================] - 34s 1s/step - loss: 1.6923 - accuracy: 0.2325 - val_loss: 1.8261 - val_accuracy: 0.3073
Epoch 4/100
25/25 [==============================] - 34s 1s/step - loss: 1.6810 - accuracy: 0.2175 - val_loss: 1.7829 - val_accuracy: 0.2656
Epoch 5/100
25/25 [==============================] - 34s 1s/step - loss: 1.6517 - accuracy: 0.2225 - val_loss: 1.7979 - val_accuracy: 0.2396
Epoch 6/100
25/25 [==============================] - 35s 1s/step - loss: 1.6633 - accuracy: 0.2225 - val_loss: 1.7933 - val_accuracy: 0.2240
Epoch 7/100
25/25 [==============================] - 35s 1s/step - loss: 1.6198 - accuracy: 0.2637 - val_loss: 1.7102 - val_accuracy: 0.3906
Epoch 8/100
2

In [29]:
model_flat_pool_drop.evaluate(test_ds)

8/8 [==============================] - 3s 272ms/step - loss: 0.6817 - accuracy: 0.7227


[0.6817080974578857, 0.72265625]

### Do warstw spłaszczonych i splotowych

In [30]:
model_flat_conv_drop = keras.models.Sequential([
    keras.layers.Conv2D(filters=96, kernel_size=(11,11), strides=(4,4), activation='relu', input_shape=(227,227,3)),
    keras.layers.Dropout(.5),
    keras.layers.MaxPool2D(pool_size=(3,3), strides=(2,2)),
    keras.layers.Conv2D(filters=256, kernel_size=(5,5), strides=(1,1), activation='relu', padding="same"),
    keras.layers.Dropout(.5),
    keras.layers.MaxPool2D(pool_size=(3,3), strides=(2,2)),
    keras.layers.Conv2D(filters=384, kernel_size=(3,3), strides=(1,1), activation='relu', padding="same"),
    keras.layers.Dropout(.5),
    keras.layers.Conv2D(filters=384, kernel_size=(3,3), strides=(1,1), activation='relu', padding="same"),
    keras.layers.Dropout(.5),
    keras.layers.Conv2D(filters=256, kernel_size=(3,3), strides=(1,1), activation='relu', padding="same"),
    keras.layers.Dropout(.5),
    keras.layers.MaxPool2D(pool_size=(3,3), strides=(2,2)),
    keras.layers.Flatten(),
    keras.layers.Dense(4096, activation='relu'),
    keras.layers.Dropout(.5),
    keras.layers.Dense(4096, activation='relu'),
    keras.layers.Dropout(.5),
    keras.layers.Dense(10, activation='softmax')
])

In [31]:
model_flat_conv_drop.compile(loss='sparse_categorical_crossentropy', optimizer=tf.optimizers.SGD(lr=.001), metrics=['accuracy'])
model_flat_conv_drop.summary()

Model: "sequential_4"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 conv2d_20 (Conv2D)          (None, 55, 55, 96)        34944     
                                                                 
 dropout_15 (Dropout)        (None, 55, 55, 96)        0         
                                                                 
 max_pooling2d_12 (MaxPoolin  (None, 27, 27, 96)       0         
 g2D)                                                            
                                                                 
 conv2d_21 (Conv2D)          (None, 27, 27, 256)       614656    
                                                                 
 dropout_16 (Dropout)        (None, 27, 27, 256)       0         
                                                                 
 max_pooling2d_13 (MaxPoolin  (None, 13, 13, 256)      0         
 g2D)                                                 

In [32]:
model_flat_conv_drop.fit(train_ds,
          epochs=100,
          validation_data=validation_ds,
          validation_freq=1,
          callbacks=[tensorboard_cb])

Epoch 1/100
25/25 [==============================] - 38s 1s/step - loss: 1.8599 - accuracy: 0.2175 - val_loss: 2.1514 - val_accuracy: 0.2500
Epoch 2/100
25/25 [==============================] - 36s 1s/step - loss: 1.6948 - accuracy: 0.2500 - val_loss: 2.1303 - val_accuracy: 0.2656
Epoch 3/100
25/25 [==============================] - 36s 1s/step - loss: 1.5830 - accuracy: 0.3088 - val_loss: 2.0759 - val_accuracy: 0.1875
Epoch 4/100
25/25 [==============================] - 36s 1s/step - loss: 1.5122 - accuracy: 0.3425 - val_loss: 2.0394 - val_accuracy: 0.2344
Epoch 5/100
25/25 [==============================] - 36s 1s/step - loss: 1.4322 - accuracy: 0.3787 - val_loss: 1.9146 - val_accuracy: 0.3594
Epoch 6/100
25/25 [==============================] - 36s 1s/step - loss: 1.2522 - accuracy: 0.4450 - val_loss: 1.9610 - val_accuracy: 0.2448
Epoch 7/100
25/25 [==============================] - 35s 1s/step - loss: 1.2729 - accuracy: 0.4475 - val_loss: 1.7461 - val_accuracy: 0.4792
Epoch 8/100
2

In [33]:
model_flat_conv_drop.evaluate(test_ds)

8/8 [==============================] - 4s 260ms/step - loss: 0.9765 - accuracy: 0.6445


[0.9765039086341858, 0.64453125]

### Do warstw maxpooling i splotowych

In [34]:
model_pool_conv_drop = keras.models.Sequential([
    keras.layers.Conv2D(filters=96, kernel_size=(11,11), strides=(4,4), activation='relu', input_shape=(227,227,3)),
    keras.layers.Dropout(.5),
    keras.layers.MaxPool2D(pool_size=(3,3), strides=(2,2)),
    keras.layers.Dropout(.5),
    keras.layers.Conv2D(filters=256, kernel_size=(5,5), strides=(1,1), activation='relu', padding="same"),
    keras.layers.Dropout(.5),
    keras.layers.MaxPool2D(pool_size=(3,3), strides=(2,2)),
    keras.layers.Dropout(.5),
    keras.layers.Conv2D(filters=384, kernel_size=(3,3), strides=(1,1), activation='relu', padding="same"),
    keras.layers.Dropout(.5),
    keras.layers.Conv2D(filters=384, kernel_size=(3,3), strides=(1,1), activation='relu', padding="same"),
    keras.layers.Dropout(.5),
    keras.layers.Conv2D(filters=256, kernel_size=(3,3), strides=(1,1), activation='relu', padding="same"),
    keras.layers.Dropout(.5),
    keras.layers.MaxPool2D(pool_size=(3,3), strides=(2,2)),
    keras.layers.Dropout(.5),
    keras.layers.Flatten(),
    keras.layers.Dense(4096, activation='relu'),
    keras.layers.Dense(4096, activation='relu'),
    keras.layers.Dense(10, activation='softmax')
])

In [35]:
model_pool_conv_drop.compile(loss='sparse_categorical_crossentropy', optimizer=tf.optimizers.SGD(lr=.001), metrics=['accuracy'])
model_pool_conv_drop.summary()

Model: "sequential_5"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 conv2d_25 (Conv2D)          (None, 55, 55, 96)        34944     
                                                                 
 dropout_22 (Dropout)        (None, 55, 55, 96)        0         
                                                                 
 max_pooling2d_15 (MaxPoolin  (None, 27, 27, 96)       0         
 g2D)                                                            
                                                                 
 dropout_23 (Dropout)        (None, 27, 27, 96)        0         
                                                                 
 conv2d_26 (Conv2D)          (None, 27, 27, 256)       614656    
                                                                 
 dropout_24 (Dropout)        (None, 27, 27, 256)       0         
                                                      

In [36]:
model_pool_conv_drop.fit(train_ds,
          epochs=100,
          validation_data=validation_ds,
          validation_freq=1,
          callbacks=[tensorboard_cb])

Epoch 1/100
25/25 [==============================] - 38s 1s/step - loss: 1.8169 - accuracy: 0.2000 - val_loss: 2.2493 - val_accuracy: 0.1875
Epoch 2/100
25/25 [==============================] - 36s 1s/step - loss: 1.6415 - accuracy: 0.2438 - val_loss: 2.2203 - val_accuracy: 0.1979
Epoch 3/100
25/25 [==============================] - 36s 1s/step - loss: 1.5604 - accuracy: 0.2862 - val_loss: 2.1751 - val_accuracy: 0.2083
Epoch 4/100
25/25 [==============================] - 36s 1s/step - loss: 1.5147 - accuracy: 0.3113 - val_loss: 2.1321 - val_accuracy: 0.1927
Epoch 5/100
25/25 [==============================] - 36s 1s/step - loss: 1.3579 - accuracy: 0.4162 - val_loss: 2.0497 - val_accuracy: 0.2865
Epoch 6/100
25/25 [==============================] - 36s 1s/step - loss: 1.3016 - accuracy: 0.4525 - val_loss: 2.0358 - val_accuracy: 0.2344
Epoch 7/100
25/25 [==============================] - 36s 1s/step - loss: 1.2612 - accuracy: 0.4512 - val_loss: 1.9886 - val_accuracy: 0.2292
Epoch 8/100
2

In [37]:
model_pool_conv_drop.evaluate(test_ds)

8/8 [==============================] - 2s 269ms/step - loss: 2.1567 - accuracy: 0.2891


[2.1567039489746094, 0.2890625]

### Do warstw spłaszczonych, maxpooling i splotowych

In [38]:
model_drop = keras.models.Sequential([
    keras.layers.Conv2D(filters=96, kernel_size=(11,11), strides=(4,4), activation='relu', input_shape=(227,227,3)),
    keras.layers.Dropout(.5),
    keras.layers.MaxPool2D(pool_size=(3,3), strides=(2,2)),
    keras.layers.Dropout(.5),
    keras.layers.Conv2D(filters=256, kernel_size=(5,5), strides=(1,1), activation='relu', padding="same"),
    keras.layers.Dropout(.5),
    keras.layers.MaxPool2D(pool_size=(3,3), strides=(2,2)),
    keras.layers.Dropout(.5),
    keras.layers.Conv2D(filters=384, kernel_size=(3,3), strides=(1,1), activation='relu', padding="same"),
    keras.layers.Dropout(.5),
    keras.layers.Conv2D(filters=384, kernel_size=(3,3), strides=(1,1), activation='relu', padding="same"),
    keras.layers.Dropout(.5),
    keras.layers.Conv2D(filters=256, kernel_size=(3,3), strides=(1,1), activation='relu', padding="same"),
    keras.layers.Dropout(.5),
    keras.layers.MaxPool2D(pool_size=(3,3), strides=(2,2)),
    keras.layers.Dropout(.5),
    keras.layers.Flatten(),
    keras.layers.Dense(4096, activation='relu'),
    keras.layers.Dropout(.5),
    keras.layers.Dense(4096, activation='relu'),
    keras.layers.Dropout(.5),
    keras.layers.Dense(10, activation='softmax')
])

In [39]:
model_drop.compile(loss='sparse_categorical_crossentropy', optimizer=tf.optimizers.SGD(lr=.001), metrics=['accuracy'])
model_drop.summary()

Model: "sequential_6"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 conv2d_30 (Conv2D)          (None, 55, 55, 96)        34944     
                                                                 
 dropout_30 (Dropout)        (None, 55, 55, 96)        0         
                                                                 
 max_pooling2d_18 (MaxPoolin  (None, 27, 27, 96)       0         
 g2D)                                                            
                                                                 
 dropout_31 (Dropout)        (None, 27, 27, 96)        0         
                                                                 
 conv2d_31 (Conv2D)          (None, 27, 27, 256)       614656    
                                                                 
 dropout_32 (Dropout)        (None, 27, 27, 256)       0         
                                                      

In [40]:
model_drop.fit(train_ds,
          epochs=100,
          validation_data=validation_ds,
          validation_freq=1,
          callbacks=[tensorboard_cb])

Epoch 1/100
25/25 [==============================] - 39s 1s/step - loss: 1.9247 - accuracy: 0.1900 - val_loss: 2.2491 - val_accuracy: 0.1875
Epoch 2/100
25/25 [==============================] - 38s 2s/step - loss: 1.7130 - accuracy: 0.2062 - val_loss: 2.2165 - val_accuracy: 0.1771
Epoch 3/100
25/25 [==============================] - 39s 2s/step - loss: 1.6761 - accuracy: 0.2350 - val_loss: 2.1936 - val_accuracy: 0.2292
Epoch 4/100
25/25 [==============================] - 37s 1s/step - loss: 1.6171 - accuracy: 0.2500 - val_loss: 2.1467 - val_accuracy: 0.1927
Epoch 5/100
25/25 [==============================] - 37s 1s/step - loss: 1.5317 - accuracy: 0.3175 - val_loss: 2.0777 - val_accuracy: 0.1927
Epoch 6/100
25/25 [==============================] - 37s 1s/step - loss: 1.4446 - accuracy: 0.3938 - val_loss: 2.0430 - val_accuracy: 0.1979
Epoch 7/100
25/25 [==============================] - 37s 1s/step - loss: 1.3851 - accuracy: 0.3787 - val_loss: 1.9749 - val_accuracy: 0.2188
Epoch 8/100
2

In [41]:
model_drop.evaluate(test_ds)

8/8 [==============================] - 3s 269ms/step - loss: 2.6610 - accuracy: 0.2227


[2.6609723567962646, 0.22265625]

## Batch Regularization

### Bez dropoutu

In [42]:
model_batch = keras.models.Sequential([
    keras.layers.Conv2D(filters=96, kernel_size=(11,11), strides=(4,4), activation='relu', input_shape=(227,227,3)),
    keras.layers.BatchNormalization(),
    keras.layers.MaxPool2D(pool_size=(3,3), strides=(2,2)),
    keras.layers.Conv2D(filters=256, kernel_size=(5,5), strides=(1,1), activation='relu', padding="same"),
    keras.layers.BatchNormalization(),
    keras.layers.MaxPool2D(pool_size=(3,3), strides=(2,2)),
    keras.layers.Conv2D(filters=384, kernel_size=(3,3), strides=(1,1), activation='relu', padding="same"),
    keras.layers.BatchNormalization(),
    keras.layers.Conv2D(filters=384, kernel_size=(3,3), strides=(1,1), activation='relu', padding="same"),
    keras.layers.BatchNormalization(),
    keras.layers.Conv2D(filters=256, kernel_size=(3,3), strides=(1,1), activation='relu', padding="same"),
    keras.layers.BatchNormalization(),
    keras.layers.MaxPool2D(pool_size=(3,3), strides=(2,2)),
    keras.layers.Flatten(),
    keras.layers.Dense(4096, activation='relu'),
    keras.layers.Dense(4096, activation='relu'),
    keras.layers.Dense(10, activation='softmax')
])

In [43]:
model_batch.compile(loss='sparse_categorical_crossentropy', optimizer=tf.optimizers.SGD(lr=.001), metrics=['accuracy'])
model_batch.summary()

Model: "sequential_7"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 conv2d_35 (Conv2D)          (None, 55, 55, 96)        34944     
                                                                 
 batch_normalization (BatchN  (None, 55, 55, 96)       384       
 ormalization)                                                   
                                                                 
 max_pooling2d_21 (MaxPoolin  (None, 27, 27, 96)       0         
 g2D)                                                            
                                                                 
 conv2d_36 (Conv2D)          (None, 27, 27, 256)       614656    
                                                                 
 batch_normalization_1 (Batc  (None, 27, 27, 256)      1024      
 hNormalization)                                                 
                                                      

In [44]:
model_batch.fit(train_ds,
          epochs=100,
          validation_data=validation_ds,
          validation_freq=1,
          callbacks=[tensorboard_cb])

Epoch 1/100
25/25 [==============================] - 40s 1s/step - loss: 3.1972 - accuracy: 0.5163 - val_loss: 2.0980 - val_accuracy: 0.1979
Epoch 2/100
25/25 [==============================] - 37s 1s/step - loss: 0.4927 - accuracy: 0.8238 - val_loss: 2.2667 - val_accuracy: 0.1823
Epoch 3/100
25/25 [==============================] - 37s 1s/step - loss: 0.2552 - accuracy: 0.9150 - val_loss: 2.7730 - val_accuracy: 0.1771
Epoch 4/100
25/25 [==============================] - 36s 1s/step - loss: 0.1681 - accuracy: 0.9475 - val_loss: 3.5623 - val_accuracy: 0.1719
Epoch 5/100
25/25 [==============================] - 36s 1s/step - loss: 0.0812 - accuracy: 0.9837 - val_loss: 4.0812 - val_accuracy: 0.1667
Epoch 6/100
25/25 [==============================] - 36s 1s/step - loss: 0.0845 - accuracy: 0.9825 - val_loss: 4.5273 - val_accuracy: 0.1771
Epoch 7/100
25/25 [==============================] - 36s 1s/step - loss: 0.0401 - accuracy: 0.9962 - val_loss: 5.9585 - val_accuracy: 0.1823
Epoch 8/100
2

In [45]:
model_batch.evaluate(test_ds)

8/8 [==============================] - 5s 294ms/step - loss: 0.2599 - accuracy: 0.9180


[0.25985682010650635, 0.91796875]

### Z dropoutem

In [46]:
model_batch_drop = keras.models.Sequential([
    keras.layers.Conv2D(filters=96, kernel_size=(11,11), strides=(4,4), activation='relu', input_shape=(227,227,3)),
    keras.layers.BatchNormalization(),
    keras.layers.Dropout(.5),
    keras.layers.MaxPool2D(pool_size=(3,3), strides=(2,2)),
    keras.layers.Dropout(.5),
    keras.layers.Conv2D(filters=256, kernel_size=(5,5), strides=(1,1), activation='relu', padding="same"),
    keras.layers.BatchNormalization(),
    keras.layers.Dropout(.5),
    keras.layers.MaxPool2D(pool_size=(3,3), strides=(2,2)),
    keras.layers.Dropout(.5),
    keras.layers.Conv2D(filters=384, kernel_size=(3,3), strides=(1,1), activation='relu', padding="same"),
    keras.layers.BatchNormalization(),
    keras.layers.Dropout(.5),
    keras.layers.Conv2D(filters=384, kernel_size=(3,3), strides=(1,1), activation='relu', padding="same"),
    keras.layers.BatchNormalization(),
    keras.layers.Dropout(.5),
    keras.layers.Conv2D(filters=256, kernel_size=(3,3), strides=(1,1), activation='relu', padding="same"),
    keras.layers.BatchNormalization(),
    keras.layers.Dropout(.5),
    keras.layers.MaxPool2D(pool_size=(3,3), strides=(2,2)),
    keras.layers.Dropout(.5),
    keras.layers.Flatten(),
    keras.layers.Dense(4096, activation='relu'),
    keras.layers.Dropout(.5),
    keras.layers.Dense(4096, activation='relu'),
    keras.layers.Dropout(.5),
    keras.layers.Dense(10, activation='softmax')
])

In [47]:
model_batch_drop.compile(loss='sparse_categorical_crossentropy', optimizer=tf.optimizers.SGD(lr=.001), metrics=['accuracy'])
model_batch_drop.summary()

Model: "sequential_8"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 conv2d_40 (Conv2D)          (None, 55, 55, 96)        34944     
                                                                 
 batch_normalization_5 (Batc  (None, 55, 55, 96)       384       
 hNormalization)                                                 
                                                                 
 dropout_40 (Dropout)        (None, 55, 55, 96)        0         
                                                                 
 max_pooling2d_24 (MaxPoolin  (None, 27, 27, 96)       0         
 g2D)                                                            
                                                                 
 dropout_41 (Dropout)        (None, 27, 27, 96)        0         
                                                                 
 conv2d_41 (Conv2D)          (None, 27, 27, 256)      

In [48]:
model_batch_drop.fit(train_ds,
          epochs=100,
          validation_data=validation_ds,
          validation_freq=1,
          callbacks=[tensorboard_cb])

Epoch 1/100
25/25 [==============================] - 42s 2s/step - loss: 18.7754 - accuracy: 0.2300 - val_loss: 3.0447 - val_accuracy: 0.2500
Epoch 2/100
25/25 [==============================] - 40s 2s/step - loss: 5.7450 - accuracy: 0.2862 - val_loss: 2.0106 - val_accuracy: 0.2031
Epoch 3/100
25/25 [==============================] - 40s 2s/step - loss: 5.0484 - accuracy: 0.2800 - val_loss: 1.8900 - val_accuracy: 0.1927
Epoch 4/100
25/25 [==============================] - 40s 2s/step - loss: 3.9955 - accuracy: 0.2988 - val_loss: 1.8577 - val_accuracy: 0.1979
Epoch 5/100
25/25 [==============================] - 40s 2s/step - loss: 4.0152 - accuracy: 0.3063 - val_loss: 1.8857 - val_accuracy: 0.1979
Epoch 6/100
25/25 [==============================] - 40s 2s/step - loss: 3.2712 - accuracy: 0.3063 - val_loss: 1.8446 - val_accuracy: 0.1250
Epoch 7/100
25/25 [==============================] - 41s 2s/step - loss: 2.5423 - accuracy: 0.3587 - val_loss: 1.8951 - val_accuracy: 0.1875
Epoch 8/100


In [49]:
model_batch_drop.evaluate(test_ds)

8/8 [==============================] - 5s 283ms/step - loss: 9.0089 - accuracy: 0.1758


[9.008861541748047, 0.17578125]